In [2]:
from bs4 import BeautifulSoup
from urllib.request import urlopen
import pandas as pd
import string

In [3]:
def tagify(key, value):
    return "<" + key + ":" + value + ">"

def process_story(soup):
    processed_story = ""
    attribute_error_counts = 0
    
    processed_story += tagify(
        "EPISODE NUMBER",
        soup.find(attrs={"class": "radio-episode-num"}).getText()[:-1],
        )
    processed_story += " "
    
    episode_name = soup.find(attrs={"class": "radio"}).find("a").getText()
    processed_story += tagify(
        "EPISODE NAME",
        episode_name,
        )
    processed_story += " "

    story = soup.findAll(attrs={"class": "act-inner"})
    for section in story:
        for speaker in section.children:
            try:
                processed_story += tagify(
                    dict(speaker.attrs)["class"][0].upper(), 
                    speaker.find("h4").getText().upper(),
                )
                processed_story += " "
                for p in speaker.findAll("p"):
                    processed_story += p.getText()
                    processed_story += " "
            except AttributeError as e:
                pass
                attribute_error_counts += 1
    
    return (episode_name, processed_story)

In [165]:
BASE_URL = 'http://www.thisamericanlife.org/radio-archives/episode/EPISODE_NUMBER/transcript'
DOWNLOAD_EPISODES = [496, 469, 454, 450, 441, 414, 411, 312, 250]
tal_text = ""
for episode in DOWNLOAD_EPISODES:
    page_url = BASE_URL.replace("EPISODE_NUMBER", str(episode))
    page = urlopen(page_url)
    soup = BeautifulSoup(page)
    tal_text += process_story(soup)
len(tal_text.split()) * 20

In [166]:
with open("tal_text.txt", "w") as tal:
    tal.write(tal_text)

In [7]:
BASE_URL = 'http://www.thisamericanlife.org/radio-archives/episode/EPISODE_NUMBER/transcript'
DOWNLOAD_EPISODES = range(396, 497)
tal_text_broad = []
for episode in DOWNLOAD_EPISODES:
    page_url = BASE_URL.replace("EPISODE_NUMBER", str(episode))
    page = urlopen(page_url)
    soup = BeautifulSoup(page)
    episode_name, episode_transcript = process_story(soup)
    tal_text_broad.append([episode_name, process_story(soup)])
    
print(tal_text_broad)

[['#1 Party School', ('#1 Party School', '<EPISODE NUMBER:396> <EPISODE NAME:#1 Party School> <INTERVIEWER:IRA GLASS> OK, Sarah. So it\'s ten to 1:00 on a Friday night in November, and we\'re sitting on your porch. And it seems pretty quiet. <SUBJECT:SARAH KOENIG> It\'s not that bad. <HOST:IRA GLASS> One of the producers of our radio show, Sarah Koenig, moved to a college town because her husband got a job teaching there. And by day, her neighborhood is like a college town that you would see in an old Hollywood film. Beautiful professors\' homes built in the \'20s and \'30s. Tree-lined streets. Gardens. But by night, we\'d been on her porch for five minutes when-- <SUBJECT:SARAH KOENIG> They seem drunk. These kids seem drunk. This couple here, they\'re sort of staggering a bit. I think he\'s like holding her up or something. <HOST:IRA GLASS> It\'s nine students walking down the middle of the street. Happens all the time. <SUBJECT:SARAH KOENIG> It\'s noisy, right? It\'s like it doesn\'t

In [12]:
df = pd.DataFrame(data=tal_text_broad, columns=["Episode Name", "Episode Transcript"])
df.head()

Episode Name  \
0                 #1 Party School   
1                            2010   
2                       Long Shot   
3                Contents Unknown   
4  Stories Pitched by Our Parents   

                                  Episode Transcript  
0  (#1 Party School, <EPISODE NUMBER:396> <EPISOD...  
1  (2010, <EPISODE NUMBER:397> <EPISODE NAME:2010...  
2  (Long Shot, <EPISODE NUMBER:398> <EPISODE NAME...  
3  (Contents Unknown, <EPISODE NUMBER:399> <EPISO...  
4  (Stories Pitched by Our Parents, <EPISODE NUMB...

In [13]:
df.to_csv("tal_text_broad.txt", index=False)